In [1]:
# May show warnings for newly imported packages if run in Colab default python environment.
# Please click the `RESTART RUNTIME` to run the following script correctly.
# The error message of conflicts is acceptable.
!pip install ffmpeg
!pip install nnabla-ext-cuda116
!git clone https://github.com/sony/nnabla-examples.git

fatal: destination path 'nnabla-examples' already exists and is not an empty directory.


In [2]:
%cd nnabla-examples/video-superresolution/tecogan

/content/nnabla-examples/video-superresolution/tecogan


In [3]:
!wget https://nnabla.org/pretrained-models/nnabla-examples/GANs/tecogan/tecogan_model.h5
!wget https://ge.in.tum.de/download/data/TecoGAN/vid3_LR.zip
!unzip vid3_LR.zip

--2023-11-29 14:00:14--  https://nnabla.org/pretrained-models/nnabla-examples/GANs/tecogan/tecogan_model.h5
Resolving nnabla.org (nnabla.org)... 13.224.14.53, 13.224.14.33, 13.224.14.36, ...
Connecting to nnabla.org (nnabla.org)|13.224.14.53|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 12306472 (12M) [binary/octet-stream]
Saving to: ‘tecogan_model.h5’

tecogan_model.h5    100%[===================>]  11.74M  70.6MB/s    in 0.2s    

2023-11-29 14:00:14 (70.6 MB/s) - ‘tecogan_model.h5’ saved [12306472/12306472]

--2023-11-29 14:00:14--  https://ge.in.tum.de/download/data/TecoGAN/vid3_LR.zip
Resolving ge.in.tum.de (ge.in.tum.de)... 129.187.254.228, 2001:4ca0:0:103::81bb:fee4
Connecting to ge.in.tum.de (ge.in.tum.de)|129.187.254.228|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 6651660 (6.3M) [application/zip]
Saving to: ‘vid3_LR.zip’

vid3_LR.zip         100%[===================>]   6.34M   420KB/s    in 16s     

2023-11-29 14:00:3

## Checking the Model with the provided Dataset

In [4]:
!python generate.py --model tecogan_model.h5 --input-dir-lr walk --output-dir results/walk
!ffmpeg -i results/walk/output_%04d.png -r 24/1 -y hr.mp4
!ffmpeg -i walk/%04d.png -r 24/1 -y lr.mp4

2023-11-29 14:00:49,070 [nnabla][INFO]: Initializing CPU extension...
/content/nnabla-examples/utils
2023-11-29 14:00:51,050 [nnabla][INFO]: Initializing CUDA extension...
2023-11-29 14:00:51,155 [nnabla][INFO]: Initializing cuDNN extension...
Frame evaluation starts!!
Warming up 5
Warming up 4
Warming up 3
Warming up 2
Warming up 1
saving image output_0001
saving image output_0002
saving image output_0003
saving image output_0004
saving image output_0005
saving image output_0006
saving image output_0007
saving image output_0008
saving image output_0009
saving image output_0010
saving image output_0011
saving image output_0012
saving image output_0013
saving image output_0014
saving image output_0015
saving image output_0016
saving image output_0017
saving image output_0018
saving image output_0019
saving image output_0020
saving image output_0021
saving image output_0022
saving image output_0023
saving image output_0024
saving image output_0025
saving image output_0026
saving image ou

Defining a custom function  to play embedded Video

In [5]:
from IPython.display import HTML
from base64 import b64encode


def play_video(filename, height=512, width=512):
    mp4 = open(filename, 'rb').read()
    data_url = "data:video/mp4;base64," + b64encode(mp4).decode()
    return HTML(f"""
    <video width={width} height={height} controls>
          <source src={data_url} type="video/mp4">
    </video>""")

Low Resolution Video

In [6]:
play_video("lr.mp4")

High Resolution Video

In [7]:
play_video("hr.mp4")

# Testing the Model with Custom inputs

Using Google files to enable the upload/download features

In [8]:
from google.colab import files

video = files.upload()

Saving test1.mp4 to test1.mp4


Renaming the input videos for usage convenience

In [9]:
import os
ext = os.path.splitext(list(video.keys())[-1])[-1]
os.rename(list(video.keys())[-1], "input_video{}".format(ext))
input_video = "input_video" + ext

Checking the FPS measure of the current video

In [16]:
import cv2


video = cv2.VideoCapture("input_video.mp4");

# Find OpenCV version
(major_ver, minor_ver, subminor_ver) = (cv2.__version__).split('.')

if int(major_ver)  < 3 :
    fps = video.get(cv2.cv.CV_CAP_PROP_FPS)
    print ("Frames per second using video.get(cv2.cv.CV_CAP_PROP_FPS): {0}".format(fps))
else :
    fps = video.get(cv2.CAP_PROP_FPS)
    print ("Frames per second using video.get(cv2.CAP_PROP_FPS) : {0}".format(fps))

video.release();

Frames per second using video.get(cv2.CAP_PROP_FPS) : 30.0


Converting the videos to resolution aspect ratio of width 200 and corresponding height

In [10]:
width=!ffprobe -v error -select_streams v:0 -show_entries stream=width -of csv=p=0 input_video.mp4
height=!ffprobe -v error -select_streams v:0 -show_entries stream=height -of csv=p=0 input_video.mp4
new_height = int(height[0])*200 // int(width[0])
new_height = 4*round(new_height/4)
!mkdir -p frames/input_video
!ffmpeg -i $input_video -vf "fps=30, scale=200:$new_height" frames/input_video/frame_%04d.png
!ffmpeg -i frames/input_video/frame_%04d.png -r 30/1 -y user_video_lr.mp4

ffmpeg version 4.4.2-0ubuntu0.22.04.1 Copyright (c) 2000-2021 the FFmpeg developers
  built with gcc 11 (Ubuntu 11.2.0-19ubuntu1)
  configuration: --prefix=/usr --extra-version=0ubuntu0.22.04.1 --toolchain=hardened --libdir=/usr/lib/x86_64-linux-gnu --incdir=/usr/include/x86_64-linux-gnu --arch=amd64 --enable-gpl --disable-stripping --enable-gnutls --enable-ladspa --enable-libaom --enable-libass --enable-libbluray --enable-libbs2b --enable-libcaca --enable-libcdio --enable-libcodec2 --enable-libdav1d --enable-libflite --enable-libfontconfig --enable-libfreetype --enable-libfribidi --enable-libgme --enable-libgsm --enable-libjack --enable-libmp3lame --enable-libmysofa --enable-libopenjpeg --enable-libopenmpt --enable-libopus --enable-libpulse --enable-librabbitmq --enable-librubberband --enable-libshine --enable-libsnappy --enable-libsoxr --enable-libspeex --enable-libsrt --enable-libssh --enable-libtheora --enable-libtwolame --enable-libvidstab --enable-libvorbis --enable-libvpx --enab

Applying super-resolution with TecoGAN

In [17]:
!python generate.py --model tecogan_model.h5 --input-dir-lr frames/input_video/ --output-dir results/user
!ffmpeg -i results/user/output_frame_%04d.png -i input_video.mp4 -r 30/1 -c:v libx264 -c:a aac -strict experimental -y user_video_hr.mp4


2023-11-29 14:15:30,221 [nnabla][INFO]: Initializing CPU extension...
/content/nnabla-examples/utils
2023-11-29 14:15:30,868 [nnabla][INFO]: Initializing CUDA extension...
2023-11-29 14:15:30,890 [nnabla][INFO]: Initializing cuDNN extension...
Frame evaluation starts!!
Warming up 5
Warming up 4
Warming up 3
Warming up 2
Warming up 1
saving image output_frame_0001
saving image output_frame_0002
saving image output_frame_0003
saving image output_frame_0004
saving image output_frame_0005
saving image output_frame_0006
saving image output_frame_0007
saving image output_frame_0008
saving image output_frame_0009
saving image output_frame_0010
saving image output_frame_0011
saving image output_frame_0012
saving image output_frame_0013
saving image output_frame_0014
saving image output_frame_0015
saving image output_frame_0016
saving image output_frame_0017
saving image output_frame_0018
saving image output_frame_0019
saving image output_frame_0020
saving image output_frame_0021
saving image o

In [19]:
play_video("user_video_lr.mp4")

In [18]:
play_video("user_video_hr.mp4")

## Checking Model Performance using metrics

### SSIM (Structural-Similarity)

In [14]:
!ffmpeg -i user_video_hr.mp4 -i user_video_lr.mp4 -lavfi "[0:v]scale=iw*min(800/iw\,800/ih):ih*min(800/iw\,800/ih)[a];[1:v]scale=iw*min(800/iw\,800/ih):ih*min(800/iw\,800/ih)[b];[a][b]ssim" -f null -


ffmpeg version 4.4.2-0ubuntu0.22.04.1 Copyright (c) 2000-2021 the FFmpeg developers
  built with gcc 11 (Ubuntu 11.2.0-19ubuntu1)
  configuration: --prefix=/usr --extra-version=0ubuntu0.22.04.1 --toolchain=hardened --libdir=/usr/lib/x86_64-linux-gnu --incdir=/usr/include/x86_64-linux-gnu --arch=amd64 --enable-gpl --disable-stripping --enable-gnutls --enable-ladspa --enable-libaom --enable-libass --enable-libbluray --enable-libbs2b --enable-libcaca --enable-libcdio --enable-libcodec2 --enable-libdav1d --enable-libflite --enable-libfontconfig --enable-libfreetype --enable-libfribidi --enable-libgme --enable-libgsm --enable-libjack --enable-libmp3lame --enable-libmysofa --enable-libopenjpeg --enable-libopenmpt --enable-libopus --enable-libpulse --enable-librabbitmq --enable-librubberband --enable-libshine --enable-libsnappy --enable-libsoxr --enable-libspeex --enable-libsrt --enable-libssh --enable-libtheora --enable-libtwolame --enable-libvidstab --enable-libvorbis --enable-libvpx --enab

### PSNR (Peak Signal to Noise Ratio)

In [15]:
!ffmpeg -i user_video_lr.mp4 -i user_video_hr.mp4 -lavfi "[0:v]scale=iw*min(800/iw\,800/ih):ih*min(800/iw\,800/ih)[a];[1:v]scale=iw*min(800/iw\,800/ih):ih*min(800/iw\,800/ih)[b];[a][b]psnr" -f null -


ffmpeg version 4.4.2-0ubuntu0.22.04.1 Copyright (c) 2000-2021 the FFmpeg developers
  built with gcc 11 (Ubuntu 11.2.0-19ubuntu1)
  configuration: --prefix=/usr --extra-version=0ubuntu0.22.04.1 --toolchain=hardened --libdir=/usr/lib/x86_64-linux-gnu --incdir=/usr/include/x86_64-linux-gnu --arch=amd64 --enable-gpl --disable-stripping --enable-gnutls --enable-ladspa --enable-libaom --enable-libass --enable-libbluray --enable-libbs2b --enable-libcaca --enable-libcdio --enable-libcodec2 --enable-libdav1d --enable-libflite --enable-libfontconfig --enable-libfreetype --enable-libfribidi --enable-libgme --enable-libgsm --enable-libjack --enable-libmp3lame --enable-libmysofa --enable-libopenjpeg --enable-libopenmpt --enable-libopus --enable-libpulse --enable-librabbitmq --enable-librubberband --enable-libshine --enable-libsnappy --enable-libsoxr --enable-libspeex --enable-libsrt --enable-libssh --enable-libtheora --enable-libtwolame --enable-libvidstab --enable-libvorbis --enable-libvpx --enab